## Seminarplatz-Vergabe

In folgendem Problem geht es darum, dass eine Gruppe von Studierenden einen oder mehrere Seminarplätze in einem Kurs bekommen sollen. Es 8 Seminargruppen mit insgesamt 40 Plätzen, diese sind in der Tabelle `seminar_sessions` abgelegt.

Bei einer Anmeldung einer einzelnen Person wird die Anzahl der Plätze in der Tabelle `seminar_sessions` um 1 reduziert und ein Eintrag in der Tabelle `seminar_registrations` erstellt. Dies darf natürlich nur passieren, wenn noch Plätze verfügbar sind.

Die Anzahl der vergebenen Plätze in der Tabelle `seminar_registrations` und die Anzahl der verfügbaren Plätze in der Tabelle `seminar_sessions` müssen konsistent sein, also in der Summe 40 ergeben.

In einem Lasttest mit mehreren Threads zeigt sich: Die Anzahl der vergebenen Plätze in der Tabelle `seminar_registrations` und die Anzahl der verfügbaren Plätze in der Tabelle `seminar_sessions` sind nicht konsistent! 

### Ihre Aufgabe:
Führen Sie geeignete Transaktionen ein, um die Konsistenz zu gewährleisten!

Implementierungen Sie dazu zunächst die Funktionen, die mit TODO gekennzeichnet sind, und passen Sie die Funktion `reserve_seat` an, um die Konsistenz zu gewährleisten.

Am Code des Lasttests müssen Sie nichts ändern, er dient nur dazu, das Problem zu demonstrieren.

### Bemerkungen:

- nicht jeder Durchlauf verursacht Inkonsistenzen, manchmal müssen Sie den Code mehrmals ausführen, um Inkonsistenzen zu finden
- auch Deadlocks können auftreten, diese müssen auch vermieden werden
- die User-Tabelle wurde weggelassen, da sie für das Problem nicht relevant ist
- an manchen Stellen ist der Code absichtlich etwas ineffizient gehalten, um die Inkonsistenzen zu begünstigen (z.B. würden Probleme mit Inkonsistenzen seltener auftreten, wenn die Query `UPDATE seminar_sessions SET seats = seats-1` lauten würde).



In [ ]:
import psycopg2
import psycopg2.extras

In [ ]:
# Datenbankverbindung herstellen
def get_connection():
  # TODO Datenbankverbindung herstellen - geben Sie hier Ihre Zugangsdaten ein
  conn = psycopg2.connect("dbname=... user=... password=...")
  
  # TODO später autocommit ausschalten
  conn.autocommit = True

  return conn

In [ ]:
# Tabelle erzeugen - immer wenn diese Zelle ausgeführt wird, wird die Tabelle neu erzeugt
conn = get_connection()
cursor = conn.cursor()
cursor.execute("""
              DROP TABLE IF EXISTS seminar_registrations CASCADE;
              DROP TABLE IF EXISTS seminar_sessions;
               
              CREATE TABLE IF NOT EXISTS seminar_sessions (
                  id SERIAL PRIMARY KEY, 
                  seats INTEGER NOT NULL
              );
                  
              INSERT INTO seminar_sessions (seats) VALUES 
                  (4), (4), (5), (5), (4), (10), (5), (3);
               
              
              CREATE TABLE IF NOT EXISTS seminar_registrations (
                  user_id INTEGER NOT NULL,
                  session_id INTEGER NOT NULL,
                  FOREIGN KEY (session_id) REFERENCES seminar_sessions(id)
              );          
""")
conn.commit()

In [ ]:
# Hilfsfunktion: Alle Seminar-Sessions ausgeben
def show_sessions():
    # TODO alle Seminar-Sessions auf der Console ausgeben
    pass

# Anzahl aller freien Plätze bestimmen
def count_free_seats():
    # TODO Anzahl freier Plätze bestimmen (Summe über die Spalte "seats")
    # und mit return zurückgeben
    pass

# Anzahl der belegten Plätze bestimmen
def count_occupied_seats():
    # TODO Anzahl belegter Plätze bestimmen (Anzahl der Einträge in der Tabelle seminar_registrations)
    # und mit return zurückgeben
    pass

# Testaufrufe

# show_sessions()
# print("freie Plätze", count_free_seats())
# print("belegte Plätze", count_occupied_seats())

In [ ]:
# Diese Funktion soll einen Platz reservieren und True zurückgeben, wenn es geklappt hat.
# Wenn kein Platz mehr frei ist, soll False zurückgegeben werden.

# TODO: Führen Sie geeignete Transaktionssteuerung ein, um sicherzustellen, dass die Funktion korrekt arbeitet.

def reserve_seat(conn, user_id, session_id):
    with conn.cursor() as cursor:
        cursor.execute("SELECT seats FROM seminar_sessions WHERE id = %s", (session_id,))
        seats = cursor.fetchone()[0]

        if seats > 0:
            cursor.execute("UPDATE seminar_sessions SET seats = %s WHERE id = %s", (seats-1, session_id,))
            cursor.execute("INSERT INTO seminar_registrations (user_id, session_id) VALUES (%s, %s)", (user_id, session_id))
            return True
        else:
            return False
        


In [ ]:
import random 

# 20 zufällige Anmeldungen durchführen - diese Funktion wird später als Thread gestartet
def random_seat_reservation(n=20):
    # jeder Thread hat seine eigene Verbindung
    conn = get_connection()
    
    # n mal einen zufälligen Platz für eine zufällige User-ID reservieren
    for _ in range(n):
        random_user_id = random.randint(1, 100)
        random_session_id = random.randint(1, 8)

        if reserve_seat(conn, random_user_id, random_session_id):
            print("User", random_user_id, "hat sich für Session", random_session_id, "angemeldet")
        else:
            print("Session", random_session_id, "ist ausgebucht")

In [ ]:
import threading

# Diese Funktion gibt Informationen über die Belegung der Seminare aus
def print_info():
    print('-'*20)
    
    free_seats = count_free_seats()
    occupied_seats = count_occupied_seats()

    print("Freie Plätze:", free_seats)
    print("Belegte Plätze:", occupied_seats)
    print("Gesamt:", free_seats + occupied_seats)
    
    if free_seats + occupied_seats == 40:
        print("Platzanzahl ist konsistent!")
    else:
        print("Platzanzahl ist inkonsistent!")

    print('-'*20)

# -------------------------------------------------------------------------
# Mini-Lasttest, 5 Threads starten, die jeweils 20 Reservierungen vornehmen
# -------------------------------------------------------------------------

print("Vor dem Lasttest:")
print_info()

threads = [ threading.Thread(target=random_seat_reservation) for _ in range(5)]

# Threads starten
for t in threads:
    t.start()

# Auf das Ende der Threads warten
for t in threads:
    t.join()

    
print("Nach dem Lasttest:")
print_info()